In [11]:
# importing libraries
import numpy as np
import pandas as pd
from pathlib import Path
import hvplot.pandas
import warnings
warnings.filterwarnings("ignore", category=FutureWarning)
import time
from sklearn.metrics import r2_score
from sklearn.preprocessing import StandardScaler
from tensorflow.keras.layers import Dense
from tensorflow.keras.models import Sequential
from tensorflow.keras.metrics import MeanSquaredError
from pandas.tseries.offsets import DateOffset
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from bokeh.models.formatters import NumeralTickFormatter

In [12]:
all_values = pd.read_csv(Path("Resources/all_values_superset.csv"))
all_values['date'] = pd.to_datetime(all_values['date'], format='%Y-%m')
all_values.set_index('date', inplace=True)
all_values.drop(columns=['All-items 8', 'All-items excluding food', 'All-items excluding food and energy'], inplace=True)
all_values.dtypes

Composite_Benchmark_SA_BANCROFT_AND_AREA                           float64
Single_Family_Benchmark_SA_BANCROFT_AND_AREA                       float64
One_Storey_Benchmark_SA_BANCROFT_AND_AREA                          float64
Two_Storey_Benchmark_SA_BANCROFT_AND_AREA                          float64
Composite_Benchmark_SA_BARRIE_AND_AREA                             float64
                                                                    ...   
Clothing and footwear                                              float64
Transportation                                                     float64
Health and personal care                                           float64
Recreation, education and reading                                  float64
Alcoholic beverages, tobacco products and recreational cannabis    float64
Length: 174, dtype: object

In [13]:
scaler_all = StandardScaler()
all_scaler = scaler_all.fit(all_values)
all_values_scaled = all_scaler.transform(all_values)

all_values_scaled_df = pd.DataFrame(all_values_scaled, columns=all_values.columns, index=all_values.index)
all_values_scaled_df.head()

Composite_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                   
2008-06-01                                 -0.835718   
2008-07-01                                 -0.841318   
2008-08-01                                 -0.855318   
2008-09-01                                 -0.873984   
2008-10-01                                 -0.880518   

            Single_Family_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                       
2008-06-01                                     -0.835718   
2008-07-01                                     -0.841318   
2008-08-01                                     -0.855318   
2008-09-01                                     -0.873984   
2008-10-01                                     -0.880518   

            One_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.953976   
2008-07-01                                  -0.979344   
2008-08-01                                  -0.990215   
2008-09-01                                  -1.020112   
2008-10-01                                  -1.027360   

            Two_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.431106   
2008-07-01                                  -0.399283   
2008-08-01                                  -0.408927   
2008-09-01                                  -0.372282   
2008-10-01                                  -0.354925   

            Composite_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.950232   
2008-07-01                               -0.957251   
2008-08-01                               -0.963768   
2008-09-01                               -0.961763   
2008-10-01                               -0.965272   

            Single_Family_Benchmark_SA_BARRIE_AND_AREA  \
date                                                     
2008-06-01                                   -0.949311   
2008-07-01                                   -0.957400   
2008-08-01                                   -0.965014   
2008-09-01                                   -0.963111   
2008-10-01                                   -0.965490   

            One_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.946094   
2008-07-01                                -0.967323   
2008-08-01                                -0.983497   
2008-09-01                                -0.978443   
2008-10-01                                -0.969850   

            Two_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.951607   
2008-07-01                                -0.950695   
2008-08-01                                -0.952063   
2008-09-01                                -0.953432   
2008-10-01                                -0.961186   

            Townhouse_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.837806   
2008-07-01                               -0.832263   
2008-08-01                               -0.827412   
2008-09-01                               -0.826026   
2008-10-01                               -0.829491   

            Apartment_Benchmark_SA_BARRIE_AND_AREA  ...       ITB  Bank Rate  \
date                                                ...                        
2008-06-01                               -0.900975  ... -0.816685   2.172972   
2008-07-01                               -0.893615  ... -0.875411   2.172972   
2008-08-01                               -0.882984  ... -0.872813   2.172972   
2008-09-01                               -0.877259  ... -0.70

In [14]:
targets = [col for col in all_values_scaled_df.columns.tolist() if col.find('Benchmark') > 0]

In [15]:
y = all_values_scaled_df[targets]

In [16]:
X = all_values_scaled_df.drop(columns = targets)

In [17]:
y.shape

(179, 161)

In [18]:
y.head()

Composite_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                   
2008-06-01                                 -0.835718   
2008-07-01                                 -0.841318   
2008-08-01                                 -0.855318   
2008-09-01                                 -0.873984   
2008-10-01                                 -0.880518   

            Single_Family_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                       
2008-06-01                                     -0.835718   
2008-07-01                                     -0.841318   
2008-08-01                                     -0.855318   
2008-09-01                                     -0.873984   
2008-10-01                                     -0.880518   

            One_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.953976   
2008-07-01                                  -0.979344   
2008-08-01                                  -0.990215   
2008-09-01                                  -1.020112   
2008-10-01                                  -1.027360   

            Two_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.431106   
2008-07-01                                  -0.399283   
2008-08-01                                  -0.408927   
2008-09-01                                  -0.372282   
2008-10-01                                  -0.354925   

            Composite_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.950232   
2008-07-01                               -0.957251   
2008-08-01                               -0.963768   
2008-09-01                               -0.961763   
2008-10-01                               -0.965272   

            Single_Family_Benchmark_SA_BARRIE_AND_AREA  \
date                                                     
2008-06-01                                   -0.949311   
2008-07-01                                   -0.957400   
2008-08-01                                   -0.965014   
2008-09-01                                   -0.963111   
2008-10-01                                   -0.965490   

            One_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.946094   
2008-07-01                                -0.967323   
2008-08-01                                -0.983497   
2008-09-01                                -0.978443   
2008-10-01                                -0.969850   

            Two_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.951607   
2008-07-01                                -0.950695   
2008-08-01                                -0.952063   
2008-09-01                                -0.953432   
2008-10-01                                -0.961186   

            Townhouse_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.837806   
2008-07-01                               -0.832263   
2008-08-01                               -0.827412   
2008-09-01                               -0.826026   
2008-10-01                               -0.829491   

            Apartment_Benchmark_SA_BARRIE_AND_AREA  ...  \
date                                                ...   
2008-06-01                               -0.900975  ...   
2008-07-01                               -0.893615  ...   
2008-08-01                               -0.882984  ...   
2008-09-01                               -0.877259  ...   
2008-10-01                               -0.910789  ...   

            Single_Family_Benchmark_SA_WINDSOR_

In [19]:
X.head()

Lumber      Wood       XHB       ITB  Bank Rate      Food  \
date                                                                      
2008-06-01 -0.672479 -0.522623 -0.941395 -0.816685   2.172972 -1.693840   
2008-07-01 -0.645519 -0.542024 -1.027669 -0.875411   2.172972 -1.641446   
2008-08-01 -0.612804 -0.504397 -0.970519 -0.872813   2.172972 -1.589052   
2008-09-01 -0.728685 -0.460303 -0.825447 -0.705470   2.172972 -1.510461   
2008-10-01 -0.891076 -0.797770 -0.949637 -0.788622   1.332881 -1.477714   

             Shelter  Household operations, furnishings and equipment  \
date                                                                    
2008-06-01 -1.168618                                        -1.911253   
2008-07-01 -1.088744                                        -1.884173   
2008-08-01 -1.048807                                        -1.884173   
2008-09-01 -1.104719                                        -1.762314   
2008-10-01 -1.096731                                        -1.789394   

            Clothing and footwear  Transportation  Health and personal care  \
date                                                                          
2008-06-01               0.170914       -0.692024                 -1.836365   
2008-07-01               0.677639       -0.692024                 -1.823707   
2008-08-01               0.360936       -0.803609                 -1.709782   
2008-09-01               0.170914       -0.810583                 -1.722441   
2008-10-01              -0.652515       -1.089543                 -1.709782   

            Recreation, education and reading  \
date                                            
2008-06-01                          -1.370649   
2008-07-01                          -1.386239   
2008-08-01                          -1.339471   
2008-09-01                          -1.355060   
2008-10-01                          -1.386239   

            Alcoholic beverages, tobacco products and recreational cannabis  
date                                                                         
2008-06-01                                          -1.488305                
2008-07-01                                          -1.493945                
2008-08-01                                          -1.499586                
2008-09-01                                          -1.471383                
2008-10-01                                          -1.471383

In [20]:
all_values_scaled_df.hvplot(
    height=800,
    width=1600
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [21]:
X_train, X_test, y_train, y_test = train_test_split(X, y)
X_train
X_test.sort_index(ascending=True, inplace=True)
y_train
y_test.sort_index(ascending=True, inplace=True)
y_test_size = y_test.shape[0]
y_test_size

45

In [22]:
# scaler = StandardScaler()

# X_scaler = scaler.fit(X_train)
# X_train_scaled = X_scaler.transform(X_train)
# X_test_scaled = X_scaler.transform(X_test)

In [23]:
# Neural network parameters
n_input_feats = len(X.columns)

n_outputs = 161

hidden_nodes_layer1 = 128
hidden_nodes_layer2 = 512
hidden_nodes_layer3 = 1024
# hidden_nodes_layer4 = 4
print(f"""
Neural Network Parameters:
--------------------------
Input Features: {n_input_feats}
Layers:         3
Layer1 Nodes:   {hidden_nodes_layer1}
Layer2 Nodes:   {hidden_nodes_layer2}
Layer3 Nodes:   {hidden_nodes_layer3}
Output Nodes:   {n_outputs}
""")


Neural Network Parameters:
--------------------------
Input Features: 13
Layers:         3
Layer1 Nodes:   128
Layer2 Nodes:   512
Layer3 Nodes:   1024
Output Nodes:   161



In [24]:
# define model
nn = Sequential()

In [25]:
# Add the first hidden layer
nn.add(Dense(
    units=hidden_nodes_layer1,
    input_dim = n_input_feats,
    activation='relu',
    name='hidden1'
))

In [26]:
# Add the second hidden layer
nn.add(Dense(
    units=hidden_nodes_layer2,
    activation='relu',
    name='hidden2'
))

In [27]:
# Add the third hidden layer
nn.add(Dense(
    units=hidden_nodes_layer3,
    activation='relu',
    name='hidden3'
))

In [28]:
# Add output
nn.add(Dense(
    n_outputs,
    activation='linear',
    name='output'
))

In [29]:
# Display the Sequential model summary
nn.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 hidden1 (Dense)             (None, 128)               1792      
                                                                 
 hidden2 (Dense)             (None, 512)               66048     
                                                                 
 hidden3 (Dense)             (None, 1024)              525312    
                                                                 
 output (Dense)              (None, 161)               165025    
                                                                 
Total params: 758,177
Trainable params: 758,177
Non-trainable params: 0
_________________________________________________________________


In [30]:
# Compile the Sequential model
nn.compile(loss='mean_squared_error', optimizer='adam', metrics=[MeanSquaredError()])

In [31]:
# Fit the model using 50 epochs and the training data
model = nn.fit(
    X_train,
    y_train,
    batch_size=10,
    validation_split=0.2,
    epochs=100
)

Epoch 1/100
11/11 [==============================] - 2s 46ms/step - loss: 0.4372 - mean_squared_error: 0.4372 - val_loss: 0.1043 - val_mean_squared_error: 0.1043
Epoch 2/100
11/11 [==============================] - 0s 17ms/step - loss: 0.1423 - mean_squared_error: 0.1423 - val_loss: 0.0937 - val_mean_squared_error: 0.0937
Epoch 3/100
11/11 [==============================] - 0s 16ms/step - loss: 0.1036 - mean_squared_error: 0.1036 - val_loss: 0.0471 - val_mean_squared_error: 0.0471
Epoch 4/100
11/11 [==============================] - 0s 16ms/step - loss: 0.0965 - mean_squared_error: 0.0965 - val_loss: 0.0487 - val_mean_squared_error: 0.0487
Epoch 5/100
11/11 [==============================] - 0s 27ms/step - loss: 0.0470 - mean_squared_error: 0.0470 - val_loss: 0.0378 - val_mean_squared_error: 0.0378
Epoch 6/100
11/11 [==============================] - 0s 20ms/step - loss: 0.0306 - mean_squared_error: 0.0306 - val_loss: 0.0245 - val_mean_squared_error: 0.0245
Epoch 7/100
11/11 [=========

In [32]:
# R2 score for training
train_pred = nn.predict(X_train)
training_r2 = r2_score(y_train.values, train_pred)
# model_loss, model_accuracy = nn.evaluate(X_test, y_test)
training_r2

5/5 [==============================] - 0s 5ms/step


0.9963811342292684

In [33]:
# Create a DataFrame with the history dictionary
model_df = pd.DataFrame(model.history, index=range(1, len(model.history["loss"]) + 1))

In [34]:
# Plot the loss
model_df.hvplot(
    y="val_loss",
    
)

:Curve   [index]   (val_loss)

In [35]:
# Plot the accuracy
model_df.hvplot(y="mean_squared_error")

:Curve   [index]   (mean_squared_error)

In [36]:
model_df[['val_loss', 'mean_squared_error']].hvplot(
    height=800,
    width=2000
)

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [37]:
predictions = nn.predict(X_test)
# predictions = nn.predict(X_test.sort_index(ascending=True))

2/2 [==============================] - 0s 3ms/step


In [38]:
# R2 score from test
test_r2 = r2_score(y_test.values, predictions)
# test_r2 = r2_score(y_test.sort_index(ascending=True).values, predictions)
test_r2

0.9934014479377135

In [39]:
all_values_pred = nn.predict(X)
all_values_pred.shape

6/6 [==============================] - 0s 6ms/step


(179, 161)

In [40]:
all_feats_pred = nn.predict(X)
all_feats_pred_df = pd.DataFrame(all_feats_pred, columns=y.columns, index=X.index)
all_preds_feats_scaled_df = pd.concat([all_feats_pred_df, X], axis=1)
all_preds_feats_descaled = all_scaler.inverse_transform(all_preds_feats_scaled_df)
all_preds_feats_descaled_df = pd.DataFrame(all_preds_feats_descaled, columns=all_preds_feats_scaled_df.columns, index=all_preds_feats_scaled_df.index)
all_preds_descaled_df = all_preds_feats_descaled_df[targets]
all_preds_descaled_df.columns = ['PRED_'+col for col in all_preds_descaled_df.columns]
all_preds_descaled_df
# all_preds_feats_descaled_df
# all_pred_real = all_values_scaled_df.copy()
# all_pred_real['Composite'] = all_values_pred
# all_values_descaled = all_scaler.inverse_transform(all_pred_real)
# all_values_descaled_df = pd.DataFrame(all_values_descaled, columns=all_values_scaled_df.columns, index=all_values_scaled_df.index)
# all_values_descaled_df
# all_values_descaled_df['Predicted'] = all_values_descaled_df['Composite']
# all_values_descaled_df['Composite'] = all_values['Composite']
# all_values_descaled_df

6/6 [==============================] - 0s 7ms/step


PRED_Composite_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                        
2008-06-01                                  160553.349091   
2008-07-01                                  161132.212511   
2008-08-01                                  163463.944767   
2008-09-01                                  163221.337119   
2008-10-01                                  160853.975916   
...                                                   ...   
2022-12-01                                  493615.019592   
2023-01-01                                  509581.156071   
2023-02-01                                  505555.972745   
2023-03-01                                  497045.233350   
2023-04-01                                  512069.575228   

            PRED_Single_Family_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                            
2008-06-01                                      160456.546155   
2008-07-01                                      161514.123658   
2008-08-01                                      163677.903651   
2008-09-01                                      163957.321704   
2008-10-01                                      161562.499581   
...                                                       ...   
2022-12-01                                      497295.600304   
2023-01-01                                      511922.486877   
2023-02-01                                      507421.399422   
2023-03-01                                      500386.754722   
2023-04-01                                      515215.012859   

            PRED_One_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                         
2008-06-01                                   150809.748195   
2008-07-01                                   151381.073948   
2008-08-01                                   153072.550815   
2008-09-01                                   154987.005256   
2008-10-01                                   155306.760832   
...                                                    ...   
2022-12-01                                   507797.927928   
2023-01-01                                   525066.097502   
2023-02-01                                   516833.822354   
2023-03-01                                   507631.003964   
2023-04-01                                   521751.618645   

            PRED_Two_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                         
2008-06-01                                   184281.774593   
2008-07-01                                   186453.235723   
2008-08-01                                   187921.192351   
2008-09-01                                   184910.742572   
2008-10-01                                   180171.665395   
...                                                    ...   
2022-12-01                                   462416.147987   
2023-01-01                                   472100.938920   
2023-02-01                                   475073.820659   
2023-03-01                                   472204.383921   
2023-04-01                                   485180.377430   

            PRED_Composite_Benchmark_SA_BARRIE_AND_AREA  \
date                                                      
2008-06-01                                245351.601405   
2008-07-01                                245933.342266   
2008-08-01                                249469.403678   
2008-09-01                                250555.633809   
2008-10-01                                247922.802568   
...                                                 ...   
2022-12-01                                764905.930267   
2023-01-01                                785512.607969   
2023-02-01                                779931.590653   
2023-03-01                                770245.586887   
2023-04-01                                790395.8

In [41]:
bancroft_pred_compare_df = pd.concat([all_preds_descaled_df.loc[:,'PRED_Composite_Benchmark_SA_BANCROFT_AND_AREA'], all_values.loc[:,'Composite_Benchmark_SA_BANCROFT_AND_AREA']], axis=1)
bancroft_pred_compare_df.hvplot(
    height=800,
    width=1600
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [42]:
oakville_pred_compare_df = pd.concat([all_preds_descaled_df.loc[:,'PRED_Two_Storey_Benchmark_SA_OAKVILLE_MILTON'], all_values.loc[:,'Two_Storey_Benchmark_SA_OAKVILLE_MILTON']], axis=1)
oakville_pred_compare_df.hvplot(
    height=800,
    width=1600
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [43]:
all_targets_pred_compare_df = pd.concat([all_preds_descaled_df, all_values[targets]], axis=1)
all_targets_pred_compare_df.hvplot(
    xlabel='Date', 
    ylabel='Price', 
    title='Actual and Predicted Index',
    height=800,
    width=1600,
    legend=False    
).opts(
    yformatter=NumeralTickFormatter(format="0,0")
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [44]:
nn_json = nn.to_json()

file_path = ("Models/model3.json")
with open(file_path, "w") as json_file:
    json_file.write(nn_json)

In [45]:
file_path = "Models/model3.h5"
nn.save_weights(file_path)

In [46]:
def mean_absolute_percentage_error(y_true, y_pred): 
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

def weighted_absolute_percentage_error(y_true, y_pred):
    return 100 / len(y_true) * np.sum(np.abs((y_true - y_pred) / y_true))

def weighted_mean_absolute_percentage_error(y_true, y_pred):
    return 100 / sum(y_true) * np.sum(np.abs(y_true - y_pred))

In [47]:
# Generate predictions
y_pred = nn.predict(X_test)

# Calculate R-Squared
r2 = r2_score(y_test, y_pred)

# Calculate Mean Absolute Error
mae = mean_absolute_error(y_test, y_pred)

# Calculate Mean Absolute Percentage Error
mape = mean_absolute_percentage_error(y_test, y_pred)

# Calculate Mean Squared Error
mse = mean_squared_error(y_test, y_pred)

# Calculate Root Mean Squared Error
rmse = np.sqrt(mse)

2/2 [==============================] - 0s 4ms/step


In [48]:
print(f"R-Squared: {r2}")
print(f"Mean Absolute Error: {mae}")
print(f"Mean Absolute Percentage Error: {mape}")
print(f"Mean Squared Error: {mse}")
print(f"Root Mean Squared Error: {rmse}")


R-Squared: 0.9934014479377135
Mean Absolute Error: 0.05411884218805003
Mean Absolute Percentage Error: 15.966261460535296
Mean Squared Error: 0.007147470484226297
Root Mean Squared Error: 0.08454271396298026
